### Disney Data Set

In [1]:
from bs4 import BeautifulSoup as bs
import requests
import pandas as pd

### Extracting info box for 1 Movie

In [2]:
r = requests.get('https://en.wikipedia.org/wiki/Toy_Story_3')
soup = bs(r.content)

In [3]:
infobox = soup.find(class_='infobox vevent')
info_rows = infobox.find_all("tr")
print(info_rows)
for row in info_rows:
    print(row)
    

[<tr><th class="infobox-above summary" colspan="2" style="font-size:110%;font-style:italic;">Toy Story 3</th></tr>, <tr><td class="infobox-image" colspan="2"><a class="image" href="/wiki/File:Toy_Story_3_poster.jpg" title="All of the toys packed close together, holding up a large numeral '3', with Buzz, who is putting a friendly arm around Woody's shoulder, and Woody holding the top of the 3."><img alt="All of the toys packed close together, holding up a large numeral '3', with Buzz, who is putting a friendly arm around Woody's shoulder, and Woody holding the top of the 3." class="thumbborder" data-file-height="326" data-file-width="220" decoding="async" height="326" src="//upload.wikimedia.org/wikipedia/en/6/69/Toy_Story_3_poster.jpg" width="220"/></a><div class="infobox-caption" style="font-size:95%;padding:0.35em 0.35em 0.25em;line-height:1.25em;">Theatrical release poster</div></td></tr>, <tr><th class="infobox-label" scope="row" style="white-space:nowrap;padding-right:0.65em;">Dir

In [4]:
def get_content_value(row_data):
    if row_data.find('li'):
        return [li.get_text(" ", strip = True).replace("\xa0", " ") for li in row_data.find_all('li')]
    else:
        return row_data.get_text(" ", strip = True).replace("\xa0", " ")
movie_info = {}
for index,row in enumerate(info_rows):
    if index == 0:
        movie_info['title'] = row.find("th").get_text()
    elif index == 1:
        continue
    else:
        content_key = row.find('th').get_text(" ", strip = True)
        content_value = get_content_value(row.find('td'))
        movie_info[content_key] = content_value


### Extracting info box for all Movies

In [5]:
r = requests.get('https://en.wikipedia.org/wiki/List_of_Walt_Disney_Pictures_films')
soup = bs(r.content)

In [6]:
movies = soup.select(".wikitable.sortable i")
movies[0].a['href']

'/wiki/Academy_Award_Review_of_Walt_Disney_Cartoons'

In [7]:
def get_content_value(row_data):
    if row_data.find('li'):
        return [li.get_text(" ", strip = True).replace("\xa0", " ") for li in row_data.find_all('li')]
    elif row_data.find("br"):
        return [text for text in row_data.stripped_strings]
    else:
        return row_data.get_text(" ", strip = True).replace("\xa0", " ")
def clean_tags(soup):
    for tag in soup.find_all(["sup", 'span']):
        tag.decompose()
def get_info_box(url):
    r = requests.get(url)
    soup = bs(r.content)
    infobox = soup.find(class_='infobox vevent')
    info_rows = infobox.find_all("tr")
    clean_tags(soup)
    movie_info = {}
    for index,row in enumerate(info_rows):
        if index == 0:
            movie_info['title'] = row.find("th").get_text()
        else:
            header = row.find('th')
            if header:
                content_key = row.find('th').get_text(" ", strip = True)
                content_value = get_content_value(row.find('td'))
                movie_info[content_key] = content_value
    return movie_info


In [8]:
get_info_box('https://en.wikipedia.org/wiki/Khoobsurat_(2014_film)')

{'title': 'Khoobsurat',
 'Directed by': 'Shashanka Ghosh',
 'Produced by': ['Rhea Kapoor', 'Anil Kapoor', 'Siddharth Roy Kapur'],
 'Written by': ['Indira Bisht', 'Juhi Chaturvedi'],
 'Starring': ['Sonam Kapoor', 'Fawad Khan'],
 'Music by': ['Songs:',
  'Sneha Khanwalkar',
  'Badshah',
  'Amaal Mallik',
  'Background Score:',
  'Simaab Sen'],
 'Cinematography': 'Tushar Kanti Ray',
 'Edited by': 'Bakul Matiyani',
 'Production companies': ['Walt Disney Pictures India',
  'Anil Kapoor Films Company'],
 'Distributed by': 'UTV Motion Pictures',
 'Release date': ['19 September 2014'],
 'Running time': '127 minutes',
 'Country': 'India',
 'Language': 'Hindi',
 'Budget': '(US$3.2 million)',
 'Box office': 'est. (US$11 million)'}

In [9]:
r = requests.get('https://en.wikipedia.org/wiki/List_of_Walt_Disney_Pictures_films')
soup = bs(r.content) 
movies = soup.select(".wikitable.sortable i a")
movie_info_list = []
base_path = "https://en.wikipedia.org/"
for index, movie in enumerate(movies):
    try:
        relative_path = movie['href']
        full_path = base_path + relative_path
        title = movie['title']
        movie_info_list.append(get_info_box(full_path))
    except Exception as e:
        print(movie.get_text())
        print(e)

Zorro the Avenger
'NoneType' object has no attribute 'find'
The Sign of Zorro
'NoneType' object has no attribute 'find'
True-Life Adventures
'NoneType' object has no attribute 'find_all'


In [10]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472'},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stuart Buchanan'],
  'Music by': ['Frank Churchill', 'P

### Saving/Loading to/from JSON

In [11]:
import json
def save_data(title, data):
    with open(title, 'w', encoding='utf-8') as f:
        json.dump(data, f, ensure_ascii=False, indent=2)

In [12]:
import json
def load_data(title):
    with open(title, encoding='utf-8') as f:
        return json.load(f)

In [13]:
save_data('disney_data_json', movie_info_list)

### Clean Data

In [14]:
movie_info_list = load_data('disney_data_json')

In [15]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472'},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stuart Buchanan'],
  'Music by': ['Frank Churchill', 'P

In [16]:
[movie.get('Running time', 'N/A') for movie in movie_info_list]

['41 minutes (74 minutes 1966 release)',
 '83 minutes',
 '88 minutes',
 '126 minutes',
 '74 minutes',
 '64 minutes',
 '70 minutes',
 '42 minutes',
 '65 min.',
 '71 minutes',
 '75 minutes',
 '94 minutes',
 '73 minutes',
 '75 minutes',
 '82 minutes',
 '68 minutes',
 '74 minutes',
 '96 minutes',
 '75 minutes',
 '84 minutes',
 '77 minutes',
 '92 minutes',
 '69 minutes',
 '81 minutes',
 ['60 minutes (VHS version)', '71 minutes (original)'],
 '127 minutes',
 '92 minutes',
 '76 minutes',
 '75 minutes',
 '73 minutes',
 '85 minutes',
 '81 minutes',
 '70 minutes',
 '90 min.',
 '80 minutes',
 '75 minutes',
 '83 minutes',
 '83 minutes',
 '72 minutes',
 '97 minutes',
 '75 minutes',
 '104 minutes',
 '93 minutes',
 '105 minutes',
 '95 minutes',
 '97 minutes',
 '134 minutes',
 '69 minutes',
 '92 minutes',
 '126 minutes',
 '79 minutes',
 '97 minutes',
 '128 minutes',
 '74 minutes',
 '91 minutes',
 '105 minutes',
 '98 minutes',
 '130 minutes',
 '89 min.',
 '93 minutes',
 '67 minutes',
 '98 minutes',
 '1

In [17]:
def minutes_to_integers(running_time):
    if running_time == 'N/A':
        return None
    if isinstance(running_time, list):
        entry = running_time[0]
        value = int(entry.split(" ")[0])
    else:
        value = int(running_time.split(" ")[0])
    return value
for movie in movie_info_list:
    movie['Running time (int)'] = minutes_to_integers(movie.get('Running time', 'N/A'))

In [18]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Collins',
   'Moroni Olsen',
   'Stuart Buchanan'],
  'Music

In [19]:
[movie.get('Budget', 'N/A') for movie in movie_info_list]

['N/A',
 '$1.49 million',
 '$2.6 million',
 '$2.28 million',
 '$600,000',
 '$950,000',
 '$858,000',
 'N/A',
 '$788,000',
 'N/A',
 '$1.35 million',
 '$2.125 million',
 'N/A',
 '$1.5 million',
 '$1.5 million',
 'N/A',
 '$2.9 million',
 '$1,800,000',
 '$3 million',
 'N/A',
 '$4 million',
 '$2 million',
 '$300,000',
 '$1.8 million',
 'N/A',
 '$5 million',
 'N/A',
 '$4 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$700,000',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$6 million',
 'under $1 million or $1,250,000',
 'N/A',
 '$2 million',
 'N/A',
 'N/A',
 '$2.5 million',
 'N/A',
 'N/A',
 '$4 million',
 '$3.6 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$3 million',
 'N/A',
 '$3 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$3 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$4.4–6 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '$4 million',
 'N/A',
 '$5 million',
 'N/A',
 'N/A',
 'N/A',
 'N/A',
 '

In [26]:
import re
number = r"\d+(,\d{3})*\.*\d*"
print(re.search(number, '790,000.35').group())

790,000.35


In [61]:
number = r"\d+(,\d{3})*\.*\d*"

amounts = r"thousand|million|billion"

value_re = rf"\${number}"

word_re = rf"\${number}(-|\sto\s|–)?({number})?\s({amounts})"

def word_to_value(word):
    value_dict = {"thousand": 1000, "million": 1000000, 'billion': 1000000000}
    return value_dict[word]

def parse_word_syntax(string):
    value_string = re.search(number, string).group()
    value = float(value_string.replace(',', ''))
    word = re.search(amounts, string, flags = re.I).group()
    word_value = word_to_value(word)
    return value*word_value
    
def parse_value_syntax(string):
    value_string = re.search(number, string).group()
    value = float(value_string.replace(',', ''))
    return value

def money_conversion(money):
    if money == 'N/A':
        return None
    if isinstance(money, list):
        money = money[0]
    word_syntax = re.search(word_re, money, flags = re.I)
    value_syntax = re.search(value_re, money)
    if word_syntax:
        return parse_word_syntax(word_syntax.group())
    elif value_syntax:
        return parse_value_syntax(value_syntax.group())
    else:
        return None
    
print(money_conversion('$790,000 million'))

790000000000.0


In [62]:
for movie in movie_info_list:
    movie['Budget (float)'] = money_conversion(movie.get('Budget', 'N/A'))
    movie['Box Office (float)'] = money_conversion(movie.get('Box office', 'N/A'))

In [65]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41,
  'Budget (float)': None,
  'Box Office (float)': 45.472},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   'Otis Harlan',
   'Scotty Mattraw',
   'Billy Gilbert',
   'Eddie Co

In [80]:
from datetime import datetime
dates = [movie.get('Release date', 'N/A') for movie in movie_info_list]

def clean_date(date):
    return date.split("(")[0].strip()
def date_conversion(date):
    if isinstance(date, list):
        date = date[0]
    if date == 'N/A':
        return None
    date_str = clean_date(date)
    fmts = ["%B %d, %Y", "%d %B, %Y"]
    for fmt in fmts:
        try:
            return datetime.strptime(date_str, fmt)
        except:
            pass
    return None
    

In [81]:
for movie in movie_info_list:
    movie['Release date (datetime)'] = date_conversion(movie.get('Release date', 'N/A'))

In [82]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41,
  'Budget (float)': None,
  'Box Office (float)': 45.472,
  'Release date (datetime)': datetime.datetime(1937, 5, 19, 0, 0)},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwell',
   'Roy Atwell',
   'Pinto Colvig',
   '

In [85]:
import pickle
def save_data_pickle(name, data):
    with open(name, 'wb') as f:
        pickle.dump(data,f)
        
def load_data_pickle(name):
    with open(name, 'rb') as f:
        return pickle.load(f)

In [87]:
save_data_pickle('disney_movie_data_cleaned_more.pickle'
                 , movie_info_list)

In [89]:
a = load_data_pickle('disney_movie_data_cleaned_more.pickle')

In [90]:
a[5]

{'title': 'Dumbo',
 'Directed by': ['Ben Sharpsteen',
  '(supervising director)',
  'Norman Ferguson',
  'Wilfred Jackson',
  'Bill Roberts',
  'Jack Kinney',
  'Samuel Armstrong'],
 'Produced by': 'Walt Disney',
 'Story by': ['Otto Englander', 'Joe Grant', 'Dick Huemer'],
 'Based on': ['Dumbo, the Flying Elephant',
  'by',
  'Helen Aberson',
  'Harold Pearl'],
 'Starring': ['Edward Brophy',
  'Verna Felton',
  'Cliff Edwards',
  'Herman Bing',
  'Sterling Holloway',
  'Margaret Wright',
  'Hall Johnson Choir'],
 'Narrated by': 'John McLeish',
 'Music by': ['Frank Churchill', 'Oliver Wallace'],
 'Production company': 'Walt Disney Productions',
 'Distributed by': 'RKO Radio Pictures',
 'Release date': ['October 23, 1941 (New York City)',
  'October 31, 1941 (U.S.)'],
 'Running time': '64 minutes',
 'Country': 'United States',
 'Language': 'English',
 'Budget': '$950,000',
 'Box office': '$1.3 million (est. United States/Canada rentals, 1941)',
 'Running time (int)': 64,
 'Budget (float)

### Attaching Scores

In [91]:
movie_info_list[-60]

{'title': 'The Jungle Book',
 'Directed by': 'Jon Favreau',
 'Produced by': ['Jon Favreau', 'Brigham Taylor'],
 'Written by': 'Justin Marks',
 'Based on': ['The Jungle Book', 'by', 'Rudyard Kipling'],
 'Starring': ['Bill Murray',
  'Ben Kingsley',
  'Idris Elba',
  "Lupita Nyong'o",
  'Scarlett Johansson',
  'Giancarlo Esposito',
  'Christopher Walken',
  'Neel Sethi'],
 'Music by': 'John Debney',
 'Cinematography': 'Bill Pope',
 'Edited by': 'Mark Livolsi',
 'Production companies': ['Walt Disney Pictures', 'Fairview Entertainment'],
 'Distributed by': ['Walt Disney Studios', 'Motion Pictures'],
 'Release date': ['April 4, 2016 ( El Capitan Theatre )',
  'April 15, 2016 (United States)'],
 'Running time': '106 minutes',
 'Country': 'United States',
 'Language': 'English',
 'Budget': '$175–177 million',
 'Box office': '$966.6 million',
 'Running time (int)': 106,
 'Budget (float)': 175000000.0,
 'Box Office (float)': 966600000.0,
 'Release date (datetime)': datetime.datetime(2016, 4, 4,

In [140]:
import requests
import urllib
import os
def get_omdb_info(title):
    base_url = "http://www.omdbapi.com/?"
    parameters = {"apikey": 'd1e0d810', 't': title}
    params_encoded = urllib.parse.urlencode(parameters)
    full_url = base_url + params_encoded
    return requests.get(url=full_url).json()

def get_rotten_tomatoes_score(ombd_data):
    ratings = ombd_data.get('Ratings', [])
    for rating in ratings:
        if rating['Source'] == 'Rotten Tomatoes':
            return rating['Value']
    return None
info = get_omdb_info('into the woods')
print(get_rotten_tomatoes_score(info))

71%


In [142]:
for movie in movie_info_list:
    title = movie['title']
    ombd_data = get_omdb_info(title)
    movie['imdb'] = ombd_data.get('imdbRating', None)
    movie['metascore'] = ombd_data.get('Metascore', None)
    movie['rotten_tomatoes'] = get_rotten_tomatoes_score(ombd_data)
print(movie_info_list)

[{'title': 'Academy Award Review of ', 'Production company': 'Walt Disney Productions', 'Release date': ['May 19, 1937'], 'Running time': '41 minutes (74 minutes 1966 release)', 'Country': 'United States', 'Language': 'English', 'Box office': '$45.472', 'Running time (int)': 41, 'Budget (float)': None, 'Box Office (float)': 45.472, 'Release date (datetime)': datetime.datetime(1937, 5, 19, 0, 0), 'imdb': '7.1', 'metascore': 'N/A', 'rotten_tomatoes': None}, {'title': 'Snow White and the Seven Dwarfs', 'Directed by': ['David Hand (supervising)', 'William Cottrell', 'Wilfred Jackson', 'Larry Morey', 'Perce Pearce', 'Ben Sharpsteen'], 'Produced by': 'Walt Disney', 'Written by': ['Ted Sears', 'Richard Creedon', 'Otto Englander', 'Dick Rickard', 'Earl Hurd', 'Merrill De Maris', 'Dorothy Ann Blank', 'Webb Smith'], 'Based on': ['Snow White', 'by The', 'Brothers Grimm'], 'Starring': ['Adriana Caselotti', 'Lucille La Verne', 'Harry Stockwell', 'Roy Atwell', 'Pinto Colvig', 'Otis Harlan', 'Scotty 

In [143]:
movie_info_list[-60]

{'title': 'The Jungle Book',
 'Directed by': 'Jon Favreau',
 'Produced by': ['Jon Favreau', 'Brigham Taylor'],
 'Written by': 'Justin Marks',
 'Based on': ['The Jungle Book', 'by', 'Rudyard Kipling'],
 'Starring': ['Bill Murray',
  'Ben Kingsley',
  'Idris Elba',
  "Lupita Nyong'o",
  'Scarlett Johansson',
  'Giancarlo Esposito',
  'Christopher Walken',
  'Neel Sethi'],
 'Music by': 'John Debney',
 'Cinematography': 'Bill Pope',
 'Edited by': 'Mark Livolsi',
 'Production companies': ['Walt Disney Pictures', 'Fairview Entertainment'],
 'Distributed by': ['Walt Disney Studios', 'Motion Pictures'],
 'Release date': ['April 4, 2016 ( El Capitan Theatre )',
  'April 15, 2016 (United States)'],
 'Running time': '106 minutes',
 'Country': 'United States',
 'Language': 'English',
 'Budget': '$175–177 million',
 'Box office': '$966.6 million',
 'Running time (int)': 106,
 'Budget (float)': 175000000.0,
 'Box Office (float)': 966600000.0,
 'Release date (datetime)': datetime.datetime(2016, 4, 4,

In [144]:
save_data_pickle('disney_movie_data_final.pickle'
                 , movie_info_list)

### Saving as JSON & CSV

In [146]:
movie_info_list

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41,
  'Budget (float)': None,
  'Box Office (float)': 45.472,
  'Release date (datetime)': datetime.datetime(1937, 5, 19, 0, 0),
  'imdb': '7.1',
  'metascore': 'N/A',
  'rotten_tomatoes': None},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Vern

In [147]:
movie_info_copy = [movie.copy() for movie in movie_info_list]

In [148]:
for movie in movie_info_copy:
    current_date = movie['Release date (datetime)']
    if current_date:
        movie['Release date (datetime)'] = current_date.strftime("%B %d, %Y")
    else:
        movie['Release date (datetime)'] = None

In [149]:
movie_info_copy

[{'title': 'Academy Award Review of ',
  'Production company': 'Walt Disney Productions',
  'Release date': ['May 19, 1937'],
  'Running time': '41 minutes (74 minutes 1966 release)',
  'Country': 'United States',
  'Language': 'English',
  'Box office': '$45.472',
  'Running time (int)': 41,
  'Budget (float)': None,
  'Box Office (float)': 45.472,
  'Release date (datetime)': 'May 19, 1937',
  'imdb': '7.1',
  'metascore': 'N/A',
  'rotten_tomatoes': None},
 {'title': 'Snow White and the Seven Dwarfs',
  'Directed by': ['David Hand (supervising)',
   'William Cottrell',
   'Wilfred Jackson',
   'Larry Morey',
   'Perce Pearce',
   'Ben Sharpsteen'],
  'Produced by': 'Walt Disney',
  'Written by': ['Ted Sears',
   'Richard Creedon',
   'Otto Englander',
   'Dick Rickard',
   'Earl Hurd',
   'Merrill De Maris',
   'Dorothy Ann Blank',
   'Webb Smith'],
  'Based on': ['Snow White', 'by The', 'Brothers Grimm'],
  'Starring': ['Adriana Caselotti',
   'Lucille La Verne',
   'Harry Stockwel

In [151]:
save_data('disney_data_final.json', movie_info_copy)

In [152]:
import pandas as pd

In [156]:
df = pd.DataFrame(movie_info_list)

In [157]:
df.head()

title       Production company  \
0         Academy Award Review of   Walt Disney Productions   
1  Snow White and the Seven Dwarfs  Walt Disney Productions   
2                        Pinocchio  Walt Disney Productions   
3                         Fantasia  Walt Disney Productions   
4             The Reluctant Dragon  Walt Disney Productions   

                                        Release date  \
0                                     [May 19, 1937]   
1  [December 21, 1937 ( Carthay Circle Theatre , ...   
2  [February 7, 1940 ( Center Theatre ), February...   
3                                [November 13, 1940]   
4                                    [June 27, 1941]   

                           Running time        Country Language  \
0  41 minutes (74 minutes 1966 release)  United States  English   
1                            83 minutes  United States  English   
2                            88 minutes  United States  English   
3                           126 minutes  United States  English   
4                            74 minutes  United States  English   

                     Box office  Running time (int)  Budget (float)  \
0                       $45.472                41.0             NaN   
1                  $418 million                83.0       1490000.0   
2                  $164 million                88.0       2600000.0   
3           $76.4–$83.3 million               126.0       2280000.0   
4  $960,000 (worldwide rentals)                74.0        600000.0   

   Box Office (float)  ... Languages Screenplay by Countries  \
0        4.547200e+01  ...       NaN           NaN       NaN   
1        4.180000e+08  ...       NaN           NaN       NaN   
2        1.640000e+08  ...       NaN           NaN       NaN   
3        8.330000e+07  ...       NaN           NaN       NaN   
4        9.600000e+05  ...       NaN           NaN       NaN   

  Production companies Japanese Hepburn Adaptation by Animation by  \
0                  NaN      NaN     NaN           NaN          NaN   
1                  NaN      NaN     NaN           NaN          NaN   
2                  NaN      NaN     NaN           NaN          NaN   
3                  NaN      NaN     NaN           NaN          NaN   
4                  NaN      NaN     NaN           NaN          NaN   

  Traditional Simplified  
0         NaN        NaN  
1         NaN        NaN  
2         NaN        NaN  
3         NaN        NaN  
4         NaN        NaN  

[5 rows x 36 columns]

In [158]:
df.to_csv('disney_movie_data_final.csv')